!pip install numpy==1.26.3

# 베이스라인 정리
### 1. LDA
### 2. NeuralLDA(AVITM)
### 3. ETM
### 4. CTM
### 5. Top2vec
### 6. ClusterTM
### 7. BERTopic

In [113]:
import os

# 원하는 저장 경로를 변수에 저장 
desired_cache_path = "/mnt/ssd1/don_ssd1/twitter_crawling_don/UTopic/hub" # 본인 mnt 디렉토리 주소 입력

# TRANSFORMERS_CACHE 환경변수 설정
os.environ["TRANSFORMERS_CACHE"] = desired_cache_path

In [3]:
import os
import re
import string
from tqdm import tqdm
import numpy as np
import torch
from torch.utils.data import Dataset
from transformers import AutoTokenizer
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.stem import WordNetLemmatizer
from sentence_transformers import SentenceTransformer
from data import *
from data import TwitterDataset, RedditDataset, YoutubeDataset, BertDataset
from coherence import get_topic_coherence

import pandas as pd
import torch.nn.functional as F
from sklearn.metrics import mutual_info_score
from torch.utils.data import DataLoader

import re
import os
import time
import argparse
import string
import torch
import torch.nn as nn
import torch.nn.functional as F
import gensim.downloader
import itertools

from sentence_transformers import SentenceTransformer

import numpy as np
from tqdm import tqdm_notebook
from torch.utils.data import Dataset, DataLoader
from transformers import AutoTokenizer
from sklearn.datasets import fetch_20newsgroups
from nltk.corpus import stopwords

from utils import AverageMeter

import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics import mutual_info_score
from gensim.corpora.dictionary import Dictionary
from pytorch_transformers import *
import scipy.stats

from gensim.models.coherencemodel import CoherenceModel
from tqdm import tqdm
import nltk

from datetime import datetime
import gensim.downloader
from scipy.linalg import qr
from data import *
from data import TwitterDataset, RedditDataset, YoutubeDataset, BertDataset
from model import ContBertTopicExtractorAE

from data import BertDataset, Stage2Dataset
import random
from sklearn.metrics.pairwise import cosine_similarity

import warnings
warnings.filterwarnings("ignore")

%load_ext autoreload
%autoreload 2

In [4]:
args_text = '--base-model sentence-transformers/paraphrase-MiniLM-L6-v2 ' + \
            '--dataset all --n-word 30000 ' + \
            '--bsz 32 --stage-2-lr 2e-2 --stage-2-repeat 5 ' + \
            '--n-cluster 20 '

In [5]:
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "0,1" 

In [6]:
def _parse_args():
    parser = argparse.ArgumentParser(description='Contrastive topic modeling')

    #각 stage에서의 batch size
    parser.add_argument('--bsz', type=int, default=64,
                        help='Batch size')
    #data set정의 
    parser.add_argument('--dataset', default='twitter', type=str,
                        choices=['twitter', 'reddit', 'youtube','all'],
                        help='Name of the dataset')
    # 클러스터 수와 topic의 수는 20 (k==20)
    parser.add_argument('--n-cluster', default=20, type=int,
                        help='Number of clusters')
    parser.add_argument('--n-topic', type=int,
                        help='Number of topics. If not specified, use same value as --n-cluster')
    # 단어vocabulary는 2000로 setting
    parser.add_argument('--n-word', default=30000, type=int,
                        help='Number of words in vocabulary')
    
    parser.add_argument('--base-model', type=str,
                        help='Name of base model in huggingface library.')
    
    parser.add_argument('--gpus', default=[0,1,2,3], type=int, nargs='+',
                        help='List of GPU numbers to use. Use 0 by default')
   
    parser.add_argument('--dirichlet-alpha-1', type=float,
                        help='Parameter for Dirichlet distribution (Phase 1). Use 1/n_topic by default.')
 
    parser.add_argument('--coeff-2-recon', default=1.0, type=float,
                        help='Coefficient for VAE reconstruction loss (Phase 2)')
    parser.add_argument('--coeff-2-regul', default=1.0, type=float,
                        help='Coefficient for VAE KLD regularization loss (Phase 2)')
    parser.add_argument('--coeff-2-cons', default=1.0, type=float,
                        help='Coefficient for CL consistency loss (Phase 2)')
    parser.add_argument('--coeff-2-dist', default=1.0, type=float,
                        help='Coefficient for CL SWD distribution matching loss (Phase 2)')
    parser.add_argument('--dirichlet-alpha-2', type=float,
                        help='Parameter for Dirichlet distribution (Phase 2). Use same value as dirichlet-alpha-1 by default.')
    parser.add_argument('--stage-2-lr', default=2e-1, type=float,
                        help='Learning rate of phase 2')
    
    parser.add_argument('--stage-2-repeat', default=5, type=int,
                        help='Repetition count of phase 2')
    
    parser.add_argument('--result-file', type=str,
                        help='File name for result summary')
    
    
    # Check if the code is run in Jupyter notebook
    is_in_jupyter = False
    try:
        shell = get_ipython().__class__.__name__
        if shell == 'ZMQInteractiveShell':
            is_in_jupyter = True   # Jupyter notebook or qtconsole
        elif shell == 'TerminalInteractiveShell':
            is_in_jupyter = False  # Terminal running IPython
        else:
            is_in_jupyter = False  # Other type (?)
    except NameError:
        is_in_jupyter = False
    
    if is_in_jupyter:
        return parser.parse_args(args=args_text.split())
    else:
        return parser.parse_args()

In [4]:
device = torch.device("cuda:3" if torch.cuda.is_available() else "cpu")

In [7]:
from sklearn.datasets import fetch_20newsgroups
import numpy as np

# 20newsgroups 데이터셋 불러오기
dataset = fetch_20newsgroups(subset='all', remove=('headers', 'footers', 'quotes'))

# 데이터셋에서 문서와 타겟(주제) 가져오기
documents = dataset.data
targets = dataset.target
target_names = dataset.target_names

# 각 주제별로 한 개의 문서를 선택하여 출력
for i in range(len(target_names)):
    # 현재 주제와 일치하는 문서들의 인덱스 찾기
    doc_indices = np.where(targets == i)[0]
    
    # 첫 번째 문서의 인덱스 선택
    doc_idx = doc_indices[0]
    
    # 해당 문서와 주제 이름 출력
    print(f"{target_names[i]}")
    #print(f"문서 예시:\n{documents[doc_idx][:500]}")  # 첫 500자만 출력
    print("-" * 80)
# 20newsgroups 데이터셋의 주제들을 'politics', 'sport', 'tech'로 매핑하는 함수를 작성합니다.

def map_topics_to_labels(targets, target_names):
    # 주제를 라벨로 매핑하는 딕셔너리
    topic_to_label = {
        'talk.politics.guns': 'politics',
        'talk.politics.mideast': 'politics',
        'talk.politics.misc': 'politics',
        'rec.sport.baseball': 'sport',
        'rec.sport.hockey': 'sport',
        'comp.os.ms-windows.misc': 'tech',
        'comp.sys.ibm.pc.hardware': 'tech',
        'comp.sys.mac.hardware': 'tech',
        'comp.windows.x': 'tech'
    }

    # 타겟(주제) ID를 라벨로 변환
    labels = np.array([topic_to_label.get(target_names[target], "other") for target in targets])
    return labels

# 20newsgroups 데이터셋의 타겟을 'politics', 'sport', 'tech' 라벨로 매핑
mapped_labels = map_topics_to_labels(targets, target_names)

# 결과 확인을 위해 첫 10개의 매핑된 라벨을 출력
mapped_labels[:10]
# 'politics', 'sport', 'tech' 라벨을 가진 문서만 필터링하는 함수

def filter_documents(documents, labels, valid_labels):
    # 유효한 라벨을 가진 문서의 인덱스를 찾습니다.
    valid_indices = [i for i, label in enumerate(labels) if label in valid_labels]

    # 해당 인덱스의 문서만 필터링합니다.
    filtered_documents = [documents[i] for i in valid_indices]
    filtered_labels = [labels[i] for i in valid_indices]

    return filtered_documents, filtered_labels

# 'politics', 'sport', 'tech' 라벨을 가진 문서 필터링
valid_labels = ['politics', 'sport', 'tech']
filtered_documents, filtered_labels = filter_documents(documents, mapped_labels, valid_labels)

alt.atheism
--------------------------------------------------------------------------------
comp.graphics
--------------------------------------------------------------------------------
comp.os.ms-windows.misc
--------------------------------------------------------------------------------
comp.sys.ibm.pc.hardware
--------------------------------------------------------------------------------
comp.sys.mac.hardware
--------------------------------------------------------------------------------
comp.windows.x
--------------------------------------------------------------------------------
misc.forsale
--------------------------------------------------------------------------------
rec.autos
--------------------------------------------------------------------------------
rec.motorcycles
--------------------------------------------------------------------------------
rec.sport.baseball
--------------------------------------------------------------------------------
rec.sport.hockey
---

In [8]:
nyt_df = pd.read_csv('nyt-articles-2020.csv')
# 'newsdesk' 열의 라벨을 'politics', 'sport', 'tech'로 매핑하는 딕셔너리 생성
newsdesk_to_label = {
    'Science': 'tech',
    'Technology': 'tech',
    'Business': 'tech',
    'Sports': 'sport',
    'OpEd': 'politics',
    'U.S.': 'politics',
    'New York': 'politics',
    'Politics': 'politics'
}

# 매핑을 적용하여 새로운 라벨 열을 생성
nyt_df['label'] = nyt_df['newsdesk'].map(newsdesk_to_label)

# 'politics', 'sport', 'tech' 라벨을 가진 행만 필터링
filtered_nyt_df = nyt_df[nyt_df['label'].isin(['politics', 'sport', 'tech'])]

In [9]:
import os
import pandas as pd

# 데이터 폴더의 경로를 설정합니다. 이 경로는 실제 데이터 폴더의 경로로 변경해야 합니다.
data_folder_path = '/mnt/ssd1/don_ssd1/twitter_crawling_don/UTopic/data/bbc'

# 라벨별로 폴더를 정의합니다.
labels = ['politics', 'sport', 'tech']

# 각 파일을 읽어 데이터프레임에 저장합니다.
data = []
for label in labels:
    folder_path = os.path.join(data_folder_path, label)
    for filename in os.listdir(folder_path):
        file_path = os.path.join(folder_path, filename)
        with open(file_path, 'r', encoding='utf-8') as file:
            content = file.read()
            data.append({'label': label, 'document': content})

# 데이터프레임 생성
df = pd.DataFrame(data)

In [10]:
newsgroups_data = list(zip(filtered_documents, filtered_labels))
nyt_data = list(zip(filtered_nyt_df['abstract'].tolist(), filtered_nyt_df['label'].tolist()))
bbc_data = list(zip(df['document'].tolist(), df['label'].tolist()))

import random

# 샘플링 사이즈와 라벨 설정
total_sample_size = 3600
labels = ['politics', 'sport', 'tech']
platforms = ['20newsgroups', 'nyt', 'bbc']
samples_per_label = total_sample_size // len(labels)

# 데이터와 라벨, 플랫폼을 라벨별로 분리하여 저장하는 함수
def sample_by_label(data, label, num_samples, platform):
    filtered_data = [(text, lbl, platform) for text, lbl in data if lbl == label]
    return random.sample(filtered_data, min(num_samples, len(filtered_data)))

# 데이터를 훈련과 테스트로 분할하는 함수
def split_train_test(data, train_ratio=0.8):
    train_size = int(len(data) * train_ratio)
    return data[:train_size], data[train_size:]

# 훈련 데이터에서 검증 데이터 분리하는 함수
def split_train_valid(data, valid_ratio_from_train=0.1):
    valid_size = int(len(data) * valid_ratio_from_train)
    train_size = len(data) - valid_size
    return data[:train_size], data[train_size:]

train_total_text_list = []
train_total_label_list = []
valid_total_text_list = []
valid_total_label_list = []
test_total_text_list = []
test_total_label_list = []
train_total_platform_list = []
valid_total_platform_list = []
test_total_platform_list = []

# 각 데이터셋에 대해 라벨별로 샘플링
data_sources = [(newsgroups_data, '20newsgroups'), (nyt_data, 'nyt'), (bbc_data, 'bbc')]

for label in labels:
    for data, platform in data_sources:
        sampled_data = sample_by_label(data, label, samples_per_label // len(labels), platform)
        # 훈련 및 테스트 데이터 분할
        train_data, test_data = split_train_test(sampled_data)
        # 훈련 데이터에서 검증 데이터 분리
        train_data, valid_data = split_train_valid(train_data)
        # 훈련, 검증, 테스트 데이터 리스트 업데이트
        train_total_text_list.extend([text for text, lbl, plt in train_data])
        train_total_label_list.extend([lbl for text, lbl, plt in train_data])
        train_total_platform_list.extend([plt for text, lbl, plt in train_data])
        valid_total_text_list.extend([text for text, lbl, plt in valid_data])
        valid_total_label_list.extend([lbl for text, lbl, plt in valid_data])
        valid_total_platform_list.extend([plt for text, lbl, plt in valid_data])
        test_total_text_list.extend([text for text, lbl, plt in test_data])
        test_total_label_list.extend([lbl for text, lbl, plt in test_data])
        test_total_platform_list.extend([plt for text, lbl, plt in test_data])


In [11]:
class BertDataset(Dataset):
    def __init__(self, bert, text_list, platform_label, label_list, N_word, vectorizer=None, lemmatize=False):
        self.lemmatize = lemmatize
        self.nonempty_text = [text for text in text_list if len(text) > 0]
        
        # Remove new lines
        self.nonempty_text = [re.sub("\n"," ", sent) for sent in self.nonempty_text]
                
        # Remove Emails
        self.nonempty_text = [re.sub('\S*@\S*\s?', '', sent) for sent in self.nonempty_text]
        
        # Remove new line characters
        self.nonempty_text = [re.sub('\s+', ' ', sent) for sent in self.nonempty_text]
        
        # Remove distracting single quotes
        self.nonempty_text = [re.sub("\'", "", sent) for sent in self.nonempty_text]
            
        self.tokenizer = AutoTokenizer.from_pretrained(bert)
        self.model = AutoModel.from_pretrained(bert)
        self.stopwords_list = set(TfidfVectorizer(stop_words="english").get_stop_words())
        self.N_word = N_word
        
        if vectorizer == None:
            self.vectorizer = TfidfVectorizer(stop_words=None, max_features=self.N_word, token_pattern=r'\b[a-zA-Z]{2,}\b')
            self.vectorizer.fit(self.preprocess_ctm(self.nonempty_text))
        else:
            self.vectorizer = vectorizer
            
        self.org_list = []
        self.bow_list = []
        for sent in tqdm(self.nonempty_text):
            org_input = self.tokenizer(sent, padding='max_length', truncation=True, max_length=512, return_tensors='pt')
            org_input['input_ids'] = torch.squeeze(org_input['input_ids'])
            org_input['attention_mask'] = torch.squeeze(org_input['attention_mask'])
            self.org_list.append(org_input)
            self.bow_list.append(self.vectorize(sent))
        ## platform label    
        self.platform_label_list = platform_label
        self.label_list = label_list
            
        
    def vectorize(self, text):
        text = self.preprocess_ctm([text])
        vectorized_input = self.vectorizer.transform(text)
        vectorized_input = vectorized_input.toarray()
        vectorized_input = vectorized_input.astype(np.float64)

        # Get word distribution from BoW
        vectorized_input += 1e-8
        vectorized_input = vectorized_input / vectorized_input.sum(axis=1, keepdims=True)
        assert abs(vectorized_input.sum() - vectorized_input.shape[0]) < 0.01
        vectorized_label = torch.tensor(vectorized_input, dtype=torch.float)
        return vectorized_label[0]
        
        
    def preprocess_ctm(self, documents):
        preprocessed_docs_tmp = documents
        preprocessed_docs_tmp = [doc.lower() for doc in preprocessed_docs_tmp]
        preprocessed_docs_tmp = [doc.translate(
            str.maketrans(string.punctuation, ' ' * len(string.punctuation))) for doc in preprocessed_docs_tmp]
        preprocessed_docs_tmp = [' '.join([w for w in doc.split() if len(w) > 0 and w not in self.stopwords_list])
                             for doc in preprocessed_docs_tmp]
        if self.lemmatize:
            lemmatizer = WordNetLemmatizer()
            preprocessed_docs_tmp = [' '.join([lemmatizer.lemmatize(w) for w in doc.split()])
                                     for doc in preprocessed_docs_tmp]
        return preprocessed_docs_tmp    
    
    # mean_pooling 함수 정의
    def mean_pooling(self, model_output, attention_mask):
        input_mask_expanded = attention_mask.unsqueeze(-1).expand(model_output.size()).float()
        sum_embeddings = torch.sum(model_output * input_mask_expanded, 1)
        sum_mask = torch.clamp(input_mask_expanded.sum(1), min=1e-9)
        return sum_embeddings / sum_mask
    
    
    def __len__(self):
        return len(self.nonempty_text)
    

    def __getitem__(self, idx):
        sentence = self.nonempty_text[idx]
        encoded_input = self.tokenizer(sentence, padding=True, truncation=True, max_length=512, return_tensors='pt')
        
        with torch.no_grad():
            model_output = self.model(**encoded_input)
        
        # mean_pooling 함수를 사용하여 문장 임베딩의 평균을 계산
        pooled_embedding = self.mean_pooling(model_output.last_hidden_state, encoded_input['attention_mask'])

        # 임베딩과 attention mask 반환
        return self.org_list[idx], self.bow_list[idx], pooled_embedding, self.platform_label_list[idx], self.label_list[idx]


In [12]:
n_word = 30000
bert_name = "sentence-transformers/paraphrase-MiniLM-L6-v2"

In [13]:
trainds = BertDataset(bert=bert_name, text_list=train_total_text_list, platform_label=train_total_platform_list, label_list=train_total_label_list, N_word=n_word, vectorizer=None, lemmatize=True)
valds = BertDataset(bert=bert_name, text_list=valid_total_text_list, platform_label=valid_total_platform_list, label_list=valid_total_label_list, N_word=n_word, vectorizer=None, lemmatize=True)
testds = BertDataset(bert=bert_name, text_list=test_total_text_list, platform_label=test_total_platform_list, label_list=test_total_label_list, N_word=n_word, vectorizer=None, lemmatize=True)

2024-03-14 21:51:57.259573: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F AVX512_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-03-14 21:51:57.433275: I tensorflow/core/util/port.cc:104] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-03-14 21:51:58.129727: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /usr/local/cuda-11.7/lib64:
2024-03-14 21:51:58.129824: W tensorflow/compiler/xla/strea

In [14]:
# 테스트 데이터에서 문서 전처리
reference_corpus = [doc.split() for doc in testds.preprocess_ctm(testds.nonempty_text)]
platform_labels = testds.platform_label_list  # 각 문서의 플랫폼 정보

# 플랫폼 별로 문서를 분류하기 위한 딕셔너리 초기화
platform_corpora = {'bbc': [], 'nyt': [], '20newsgroups': []}

# 각 문서를 플랫폼 정보에 따라 분류
for doc, platform in zip(reference_corpus, platform_labels):
    if platform in platform_corpora:
        platform_corpora[platform].append(doc)

# 플랫폼 별로 분류된 문서 확인
bbc_texts = platform_corpora['bbc']
nyt_texts = platform_corpora['nyt']
news_texts = platform_corpora['20newsgroups']

# 각 플랫폼 별 문서 수 확인
print(f"'bbc' 문서 수: {len(bbc_texts)}")
print(f"'nyt' 문서 수: {len(nyt_texts)}")
print(f"'20newsgroups' 문서 수: {len(news_texts)}")


'bbc' 문서 수: 235
'nyt' 문서 수: 240
'20newsgroups' 문서 수: 240


# AVITM(Autoencoding Variational Inference For Topic Models)

### 참조 : https://arxiv.org/abs/1703.01488
### Github : https://github.com/akashgit/autoencoding_vi_for_topic_models

In [15]:
from pytorchavitm.datasets import BOWDataset
from pytorchavitm.avitm import AVITM

# BoW 벡터를 BOWDataset에 적용
# BoW 벡터 추출
bow_vectors = [trainds[i][1] for i in range(len(trainds))]

# BOWDataset 인스턴스 생성
bow_dataset = BOWDataset(bow_vectors, idx2token=trainds.vectorizer.get_feature_names_out())

# AVITM 모델 학습
input_size = len(trainds.vectorizer.get_feature_names_out())  # 또는 적절한 입력 크기
avitm = AVITM(input_size=input_size, n_components=20)
# 모델 초기화 및 학습
# avitm = AVITM(input_size=n_word, n_components=20)  # 필요한 하이퍼파라미터 설정
avitm.fit(bow_dataset)

# 토픽 추출 및 평가
# 토픽 추출
topics = avitm.get_topics(10)  # 각 토픽별로 상위 10개 단어 추출

# 리스트 생성
avitm_topics = []
for topic_num, words in topics.items():
    avitm_topics.append((topic_num, words))

# 결과 출력
for topic_num, words in avitm_topics:
    print(f"Topic {topic_num}: {words}")

Settings: 
               N Components: 20
               Topic Prior Mean: 0.0
               Topic Prior Variance: 0.95
               Model Type: prodLDA
               Hidden Sizes: (100, 100)
               Activation: softplus
               Dropout: 0.2
               Learn Priors: True
               Learning Rate: 0.002
               Momentum: 0.99
               Reduce On Plateau: False
               Save Dir: None
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	-

In [18]:
from torch.utils.data import Dataset
import torch
import scipy.sparse

class BOWDataset(Dataset):
    """Class to load BOW dataset."""

    def __init__(self, X, idx2token):
        """
        Initialize BOWDataset.

        Args:
            X : array-like, shape=(n_samples, n_features)
                Document word matrix.
            idx2token : list of str
                Indexed vocabulary.
        """
        self.X = X
        self.idx2token = idx2token

    def __len__(self):
        """Return length of dataset."""
        # Correctly handle sparse matrix size determination
        return self.X.shape[0]

    def __getitem__(self, i):
        """Return sample from dataset at index i."""
        # Correctly handle fetching items from a sparse matrix
        if scipy.sparse.issparse(self.X):
            X = self.X[i].toarray()  # Convert sparse matrix row to dense numpy array
        else:
            X = self.X[i]
        
        # Convert numpy array to a torch tensor
        X_tensor = torch.FloatTensor(X)
        
        return {'X': X_tensor}


In [19]:
# Assuming test_total_text_list contains your raw test documents
test_texts = [' '.join(doc.split()) for doc in test_total_text_list]  # Adjust this line according to your data preprocessing steps


In [20]:
import numpy as np
import pandas as pd
import torch
from torch.utils.data import DataLoader
from sklearn.metrics import mutual_info_score

# 테스트 데이터셋 준비
# test_bow_vectors = trainds.vectorizer.transform(test_texts)
# test_bow_dataset = BOWDataset(test_bow_vectors, idx2token=trainds.vectorizer.get_feature_names_out())

test_bow_vectors = trainds.vectorizer.transform(test_texts).toarray()

# 변환된 벡터를 사용하여 BOWDataset 인스턴스 생성
test_bow_dataset = BOWDataset(test_bow_vectors, idx2token=trainds.vectorizer.get_feature_names_out())

# 테스트 데이터셋에 대한 토픽 분포 예측
test_topic_distributions = avitm.predict(test_bow_dataset)

# 토픽 라벨 추출
test_topic_labels = torch.argmax(test_topic_distributions, dim=1).cpu().numpy()

# 플랫폼 라벨 준비
test_platform_labels = [testds[i][-1] for i in range(len(testds))]

# 플랫폼별 토픽 분포 계산
topic_dist_df_test = pd.crosstab(pd.Series(test_topic_labels, name='Topic'),
                                 pd.Series(test_platform_labels, name='Platform'), normalize='index')

# 전체 데이터셋에 대한 토픽 분포의 엔트로피 계산 (H(Y))
topic_probabilities = pd.Series(test_topic_labels).value_counts(normalize=True)
H_Y = -np.sum(topic_probabilities * np.log(topic_probabilities + 1e-10))

# 각 플랫폼별 조건부 엔트로피 계산 및 H(Y|X) 계산
H_Y_given_X_total = 0
platform_probabilities = pd.Series(test_platform_labels).value_counts(normalize=True)
for platform in platform_probabilities.index:
    platform_indices = [i for i, x in enumerate(test_platform_labels) if x == platform]
    platform_topic_labels = [test_topic_labels[i] for i in platform_indices]
    platform_topic_prob = pd.Series(platform_topic_labels).value_counts(normalize=True)
    H_Y_given_X = -np.sum(platform_topic_prob * np.log(platform_topic_prob + 1e-10))
    H_Y_given_X_total += platform_probabilities[platform] * H_Y_given_X

# 상호정보량(MI) 계산
mi = H_Y - H_Y_given_X_total

# 플랫폼 분포의 엔트로피 H(X) 계산
H_X = -np.sum(platform_probabilities * np.log(platform_probabilities + 1e-10))

# 정규화된 상호정보량(NMI) 계산
NMI = 2 * mi / (H_Y + H_X)

print("Normalized Mutual Information (NMI):", NMI)
print('H(Y):', H_Y)
print('H(Y|X):', H_Y_given_X_total)
print('Mutual Information (MI):', mi)


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

ValueError: Found input variables with inconsistent numbers of samples: [720, 715]

In [78]:
class BOWDataset(Dataset):
    """Class to load BOW dataset."""

    def __init__(self, X, idx2token):
        """
        Initialize BOWDataset.

        Args:
            X : array-like, shape=(n_samples, n_features)
                Document word matrix.
            idx2token : list of str
                Indexed vocabulary.
        """
        self.X = X
        self.idx2token = idx2token

    def __len__(self):
        """Return length of dataset."""
        # 리스트의 길이를 반환
        return len(self.X)

    def __getitem__(self, i):
        """Return sample from dataset at index i."""
        # Correctly handle fetching items from a sparse matrix
        if scipy.sparse.issparse(self.X[i]):
            X = self.X[i].toarray()  # Convert sparse matrix row to dense numpy array
        else:
            X = self.X[i]
        
        # Convert numpy array to a torch tensor
        X_tensor = torch.FloatTensor(X)
        
        return {'X': X_tensor}


In [79]:
# 테스트 데이터셋 준비
bow_vectors = [trainds[i][1] for i in range(len(trainds))]
bow_dataset = BOWDataset(bow_vectors, idx2token=trainds.vectorizer.get_feature_names_out())

# 테스트 데이터셋에 대한 토픽 분포 예측
topic_distributions = avitm.predict(bow_dataset)

# # 토픽 라벨 추출
# test_topic_labels = np.argmax(test_topic_distributions, axis=1)
# PyTorch의 argmax 메소드 사용 (GPU 상에서 직접 작업 가능)
topic_labels = torch.argmax(topic_distributions, dim=1)

# PyTorch 텐서를 CPU로 이동시킨 후 NumPy 배열로 변환
topic_labels_cpu = topic_labels.cpu().numpy()

# 토픽별 라벨 데이터 수집
topic_labels_avitm = [[] for _ in range(avitm.n_components)]  # avitm.n_components는 AVITM 모델에서 설정한 토픽 수

for doc_idx, topic in enumerate(topic_labels_cpu):
    label = train_total_label_list[doc_idx]  # 각 문서에 해당하는 실제 라벨
    topic_labels_avitm[topic].append(label)
    
# 토픽별 라벨 데이터 수집
topic_labels_avitm = [[] for _ in range(avitm.n_components)]  # avitm.n_components는 AVITM 모델에서 설정한 토픽 수

for doc_idx, topic in enumerate(topic_labels_cpu):
    label = train_total_label_list[doc_idx]  # 각 문서에 해당하는 실제 라벨
    topic_labels_avitm[topic].append(label)

# 라벨 퓨리티 계산
def calculate_label_purity(topic_labels):
    purity_scores = []
    for labels in topic_labels:
        if not labels:
            continue
        most_common_label = max(set(labels), key=labels.count)
        purity = labels.count(most_common_label) / len(labels)
        purity_scores.append(purity)
    average_purity = sum(purity_scores) / len(purity_scores) if purity_scores else 0
    return purity_scores, average_purity

# label purity 계산
purity_scores_avitm, average_purity_avitm = calculate_label_purity(topic_labels_avitm)

print("AVITM 각 토픽의 라벨 순도:", purity_scores_avitm)
print("AVITM 평균 라벨 순도:", average_purity_avitm)


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

# 헝가리안 매칭

In [118]:
# 헝가리안 매칭을 위한 함수 정의
def measure_hungarian_score(topic_dist, train_target):
    dist = topic_dist
    train_target_filtered = train_target
    flat_predict = torch.tensor(np.argmax(dist, axis=1))
    flat_target = torch.tensor(train_target_filtered).to(flat_predict.device)
    num_samples = flat_predict.shape[0]
    num_classes = dist.shape[1]
    match = _hungarian_match(flat_predict, flat_target, num_samples, num_classes)    
    reordered_preds = torch.zeros(num_samples).to(flat_predict.device)
    for pred_i, target_i in match:
        reordered_preds[flat_predict == pred_i] = int(target_i)
    acc = int((reordered_preds == flat_target.float()).sum()) / float(num_samples)
    return acc

def _hungarian_match(predicted, target, num_samples, num_classes):
    matrix = np.zeros((num_classes, num_classes), dtype=np.uint64)
    for i in range(num_samples):
        matrix[predicted[i], target[i]] += 1
    row_ind, col_ind = linear_sum_assignment(matrix.max() - matrix)

In [119]:
from pytorchavitm.datasets import BOWDataset
from pytorchavitm.avitm import AVITM
import numpy as np
import torch
from torch.utils.data import DataLoader
from scipy.optimize import linear_sum_assignment
import torch.nn.functional as F

# 데이터 로딩 및 전처리
bow_vectors = [trainds[i][1] for i in range(len(trainds))]
bow_dataset = BOWDataset(bow_vectors, idx2token=trainds.vectorizer.get_feature_names_out())

# AVITM 모델 학습
input_size = len(trainds.vectorizer.get_feature_names_out())  # 입력 크기 설정
avitm = AVITM(input_size=input_size, n_components=3)  # 토픽의 개수를 3으로 설정
avitm.fit(bow_dataset)  # 모델 학습

# 토픽 추출 및 평가
topics = avitm.get_topics(10)  # 각 토픽별로 상위 10개 단어 추출
avitm_topics = []
for topic_num, words in topics.items():
    avitm_topics.append((topic_num, words))
for topic_num, words in avitm_topics:
    print(f"Topic {topic_num}: {words}")



Settings: 
               N Components: 3
               Topic Prior Mean: 0.0
               Topic Prior Variance: 0.6666666666666667
               Model Type: prodLDA
               Hidden Sizes: (100, 100)
               Activation: softplus
               Dropout: 0.2
               Learn Priors: True
               Learning Rate: 0.002
               Momentum: 0.99
               Reduce On Plateau: False
               Save Dir: None
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork i

In [125]:
test_bow_vectors = [testds[i][1] for i in range(len(testds))]
test_bow_dataset = BOWDataset(test_bow_vectors, idx2token=testds.vectorizer.get_feature_names_out())


# 테스트 데이터셋의 토픽 분포 추출
test_topic_distributions = avitm.transform(test_bow_dataset)

# 테스트 데이터 라벨
test_labels = [testds[i][2] for i in range(len(testds))]  # testds의 구조에 따라 인덱스 조정 필요

# 라벨을 정수로 매핑
label_to_int = {label: idx for idx, label in enumerate(sorted(set(test_labels)))}
int_test_labels = np.array([label_to_int[label] for label in test_labels])

# 헝가리안 매칭을 위한 함수 정의
def measure_hungarian_score(dist, true_labels):
    num_samples = len(true_labels)
    num_classes = len(np.unique(true_labels))
    flat_predict = np.argmax(dist, axis=1)
    matrix = np.zeros((num_classes, num_classes), dtype=np.uint64)
    for i in range(num_samples):
        matrix[flat_predict[i], true_labels[i]] += 1
    row_ind, col_ind = linear_sum_assignment(matrix.max() - matrix)
    match = list(zip(row_ind, col_ind))
    reordered_preds = np.zeros(num_samples, dtype=int)
    for pred_i, target_i in match:
        reordered_preds[flat_predict == pred_i] = target_i
    acc = np.sum(reordered_preds == true_labels) / float(num_samples)
    return acc

# 정확도 계산
accuracy = measure_hungarian_score(test_topic_distributions, int_test_labels)
print(f"Test Accuracy with Hungarian Matching: {accuracy}")


AttributeError: 'Tensor' object has no attribute 'toarray'

In [126]:
# PyTorch 텐서의 리스트를 단일 텐서로 병합
test_bow_vectors_tensor = torch.stack(test_bow_vectors)

# TensorDataset과 DataLoader를 사용하여 테스트 데이터셋 준비
test_dataset = TensorDataset(test_bow_vectors_tensor)
test_loader = DataLoader(test_dataset, batch_size=128, shuffle=False)


# 테스트 데이터셋의 토픽 분포 추출
topic_distributions = []

with torch.no_grad():
    for batch_samples in test_loader:
        X = batch_samples[0]
        if avitm.USE_CUDA:
            X = X.cuda()
        _, _, _, _, _, word_dists = avitm.model(X)
        topic_distributions.append(word_dists.cpu())

# 배열로 변환
topic_distributions = torch.cat(topic_distributions, dim=0).numpy()

# 테스트 데이터셋의 실제 라벨 준비 (여기서는 예시로 int_test_target_adjusted 사용)
# int_test_target_adjusted는 미리 정의된 라벨 인덱스 배열이어야 합니다.

# 헝가리안 매칭으로 정확도 계산
from scipy.optimize import linear_sum_assignment

def measure_hungarian_score(dist, true_labels):
    num_samples = dist.shape[0]
    num_classes = np.unique(true_labels).size
    flat_predict = np.argmax(dist, axis=1)
    matrix = np.zeros((num_classes, num_classes), dtype=np.uint64)
    for i in range(num_samples):
        matrix[flat_predict[i], true_labels[i]] += 1
    row_ind, col_ind = linear_sum_assignment(matrix.max() - matrix)
    match = list(zip(row_ind, col_ind))
    reordered_preds = np.zeros(num_samples, dtype=int)
    for pred_i, target_i in match:
        reordered_preds[flat_predict == pred_i] = target_i
    acc = np.sum(reordered_preds == true_labels) / float(num_samples)
    return acc

accuracy = measure_hungarian_score(topic_distributions, int_test_target_adjusted)
print("Test Accuracy with Hungarian Matching:", accuracy)


Input size: torch.Size([128, 11996])


RuntimeError: mat1 and mat2 shapes cannot be multiplied (128x11996 and 23624x100)

In [121]:
test_topic_distributions = []
for i in range(len(test_bow_dataset)):
    bow_vector = test_bow_dataset[i]
    # 모델에 따라 입력 형태를 조정할 수 있습니다. 예를 들어, tensor로 변환하는 등의 처리가 필요할 수 있습니다.
    topic_distribution = avitm.get_topic_distribution(bow_vector)  # 가상의 메서드 호출
    test_topic_distributions.append(topic_distribution)

test_topic_distributions = np.array(test_topic_distributions)


AttributeError: 'AVITM' object has no attribute 'get_topic_distribution'

In [117]:
test_labels = [testds[i][2] for i in range(len(testds))]  # testds의 구조에 따라 인덱스 조정 필요
test_labels

KeyboardInterrupt: 

# AVITM coherence

In [21]:
topics = avitm_topics

In [22]:
# 제공된 topics 튜플 리스트를 단순한 리스트 형태로 변환하는 코드
def convert_topics_to_list(topics):
    return [words for _, words in topics]

# 함수 호출
topics = convert_topics_to_list(topics)

## BBC

In [25]:
print(get_topic_coherence(topics, bbc_texts))

{'NPMI': 0.15111819811306776, 'UCI': 0.6085487427693284, 'UMASS': -1.7341395164563487, 'CV': 0.6321367774247025, 'Topic_Diversity': 0.735}


## NYT

In [26]:
print(get_topic_coherence(topics, nyt_texts))

{'NPMI': 0.5509410563707211, 'UCI': 2.823280630070761, 'UMASS': -1.2342123009852843, 'CV': 0.6203167707694222, 'Topic_Diversity': 0.735}


## 20news

In [27]:
print(get_topic_coherence(topics, news_texts))

{'NPMI': 0.3366263408049389, 'UCI': 1.7174249034178222, 'UMASS': -1.741208388621808, 'CV': 0.6752597641671472, 'Topic_Diversity': 0.735}


# CTM(Contextualized Topic Models)

### 참조 : https://aclanthology.org/2021.acl-short.96/
### Github : https://github.com/MilaNLProc/contextualized-topic-models?tab=readme-ov-file

In [28]:
from contextualized_topic_models.models.ctm import CombinedTM
from contextualized_topic_models.utils.data_preparation import TopicModelDataPreparation
train_total_text_list
# CTM 데이터 준비
tp = TopicModelDataPreparation("stsb-distilbert-base")
training_dataset = tp.fit(text_for_contextual=train_total_text_list, text_for_bow=train_total_text_list)

# CTM 모델 생성 및 학습
n_topic = 20 # 토픽의 수 설정
ctm = CombinedTM(bow_size=len(tp.vocab), contextual_size=768, n_components=n_topic, num_epochs=20)
ctm.fit(training_dataset)

# 토픽의 상위 k개 단어 추출
top_k = 10
ctm_topics = ctm.get_topic_lists(top_k)
for topic_num, topic in enumerate(ctm_topics):
    print(f"Topic {topic_num}: {topic}")


Batches:   0%|          | 0/13 [00:00<?, ?it/s]

0it [00:00, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Epoch: [1/20]	 Seen Samples: [2560/51840]	Train Loss: 2102.9981994628906	Time: 0:00:05.326101: : 1it [00:05,  5.33s/it]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

...

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


 88%|████████▊ | 36/41 [00:06<00:00, 10.25it/s]

	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


100%|██████████| 41/41 [00:06<00:00,  6.42it/s]

Topic 0: ['hitting', 'divide', 'damaged', 'potentially', 'turning', 'angry', 'reducing', 'historic', 'clean', 'spin']
Topic 1: ['original', 'coup', 'diminishes', 'slower', 'robbing', 'transcript', 'forming', 'panicking', 'pogrom', 'internal']
Topic 2: ['to', 'it', 'are', 'and', 'the', 'that', 'in', 'of', 'is', 'for']
Topic 3: ['in', 'to', 'the', 'and', 'of', 'we', 'at', 'that', 'it', 'with']
Topic 4: ['divide', 'platform', 'religion', 'god', 'spin', 'punishments', 'wages', 'afford', 'bloody', 'spirits']
Topic 5: ['said', 'mr', 'would', 'how', 'are', 'system', 'than', 'use', 'may', 'such']
Topic 6: ['ax', 'g9v', 'b8f', 'a86', '1d9', '10', '11', 'max', '0t', 'pl']
Topic 7: ['leader', 'tony', 'blair', 'tory', 'michael', 'prime', 'howard', 'former', 'minister', 'tories']
Topic 8: ['historic', 'son', 'materials', 'earth', 'escaped', 'express', 'electorate', 'threw', 'proper', 'corrupt']
Topic 9: ['users', 'said', 'computer', 'service', 'use', 'internet', 'technology', 'its', 'digital', 'mic

In [29]:
import numpy as np
import pandas as pd
from sklearn.metrics import mutual_info_score

# 테스트 데이터셋 준비 및 토픽 분포 추출
test_dataset = tp.transform(text_for_contextual=test_total_text_list, text_for_bow=test_total_text_list)
test_topic_distributions = ctm.get_thetas(test_dataset)

# 토픽 라벨 추출
test_topic_labels = np.argmax(test_topic_distributions, axis=1)

# 플랫폼 라벨 준비
test_platform_labels = [testds[i][-1] for i in range(len(testds))]

# 플랫폼별 토픽 분포 계산
topic_dist_df_test = pd.crosstab(pd.Series(test_topic_labels, name='Topic'),
                                 pd.Series(test_platform_labels, name='Platform'), normalize='index')

# 전체 데이터셋에 대한 토픽 분포의 엔트로피 계산 (H(Y))
topic_probabilities = pd.Series(test_topic_labels).value_counts(normalize=True)
H_Y = -np.sum(topic_probabilities * np.log(topic_probabilities + 1e-10))

# 각 플랫폼별 조건부 엔트로피 계산 및 H(Y|X) 계산
H_Y_given_X_total = 0
platform_probabilities = pd.Series(test_platform_labels).value_counts(normalize=True)
for platform in platform_probabilities.index:
    platform_indices = [i for i, x in enumerate(test_platform_labels) if x == platform]
    platform_topic_labels = [test_topic_labels[i] for i in platform_indices]
    platform_topic_prob = pd.Series(platform_topic_labels).value_counts(normalize=True)
    H_Y_given_X = -np.sum(platform_topic_prob * np.log(platform_topic_prob + 1e-10))
    H_Y_given_X_total += platform_probabilities[platform] * H_Y_given_X

# 상호정보량(MI) 계산
mi = H_Y - H_Y_given_X_total

# 플랫폼 분포의 엔트로피 H(X) 계산
H_X = -np.sum(platform_probabilities * np.log(platform_probabilities + 1e-10))

# 정규화된 상호정보량(NMI) 계산
NMI = 2 * mi / (H_Y + H_X)

print("Normalized Mutual Information (NMI):", NMI)
print('H(Y):', H_Y)
print('H(Y|X):', H_Y_given_X_total)
print('Mutual Information (MI):', mi)


Batches:   0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/12 [00:00<?, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

  8%|▊         | 1/12 [00:05<01:01,  5.56s/it]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


100%|██████████| 12/12 [00:06<00:00,  1.99it/s]


Normalized Mutual Information (NMI): 0.13651955522404483
H(Y): 2.898977421138974
H(Y|X): 2.6261061824967737
Mutual Information (MI): 0.2728712386422001


ValueError: Found input variables with inconsistent numbers of samples: [720, 715]

In [30]:
# 주제 다양성 계산 함수
def calculate_topic_diversity(topic_words_list):
    all_words = set()
    for words in ctm_topics:
        all_words.update(words)
    unique_words_count = len(all_words)
    total_words_count = sum(len(words) for words in ctm_topics)
    return unique_words_count / total_words_count

# 주제 다양성 계산
bert_topic_diversity = calculate_topic_diversity(ctm_topics)
print("CTM Diversity:", bert_topic_diversity)

BERTopic Diversity: 0.775


In [80]:
def assign_topics_to_documents_ctm(ctm_model, dataset):
    topic_assignments = []
    # 모든 문서에 대한 토픽 분포를 얻음
    topic_distributions = ctm_model.get_thetas(dataset)
    
    # 가장 확률이 높은 토픽을 선택
    for doc_distribution in topic_distributions:
        assigned_topic = doc_distribution.argmax()
        topic_assignments.append(assigned_topic)
    
    return topic_assignments
# 문서에 대한 토픽 할당
document_topics_ctm = assign_topics_to_documents_ctm(ctm, training_dataset)

# 토픽별 라벨 데이터 수집
topic_labels_ctm = [[] for _ in range(n_topic)]
for doc_idx, topic in enumerate(document_topics_ctm):
    label = train_total_label_list[doc_idx]  # 문서에 해당하는 라벨
    topic_labels_ctm[topic].append(label)

# 라벨 순도 계산
purity_scores_ctm, average_purity_ctm = calculate_label_purity(topic_labels_ctm)

print("CTM 각 토픽의 라벨 순도:", purity_scores_ctm)
print("CTM 평균 라벨 순도:", average_purity_ctm)


  0%|          | 0/41 [00:00<?, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

 98%|█████████▊| 40/41 [00:08<00:00, 11.23it/s]

	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


100%|██████████| 41/41 [00:08<00:00,  4.82it/s]

CTM 각 토픽의 라벨 순도: [0.3972602739726027, 0.39436619718309857, 0.5230769230769231, 0.4909090909090909, 0.34965034965034963, 0.6545454545454545, 0.6707317073170732, 0.7708333333333334, 0.4540229885057471, 0.6702127659574468, 0.40350877192982454, 0.3829787234042553, 0.7513227513227513, 0.38372093023255816, 0.6451612903225806, 0.8064516129032258, 0.3744292237442922, 0.8717948717948718, 0.8, 0.9891304347826086]
CTM 평균 라벨 순도: 0.5892053847444044


# CTM coherence

In [31]:
topics = ctm_topics

## ALL

In [15]:
print(get_topic_coherence(topics, texts))

{'NPMI': 0.36857488086396883, 'UCI': 2.7989392619043745, 'UMASS': -2.564512860921594, 'CV': 0.7071284688608676, 'Topic_Diversity': 0.845}


## BBC

In [32]:
print(get_topic_coherence(topics, bbc_texts))

{'NPMI': 0.31454735065129785, 'UCI': 1.4032365378276301, 'UMASS': -1.423590396953202, 'CV': 0.7872195600465225, 'Topic_Diversity': 0.775}


## NYT

In [33]:
print(get_topic_coherence(topics, nyt_texts))

{'NPMI': 0.6843969776497915, 'UCI': 3.605049413588602, 'UMASS': -0.9702157963201326, 'CV': 0.7629180534804517, 'Topic_Diversity': 0.775}


## 20NEWS

In [34]:
print(get_topic_coherence(topics, news_texts))

{'NPMI': 0.42559609788331776, 'UCI': 2.1841415285407906, 'UMASS': -1.4588080184798806, 'CV': 0.7225426084625358, 'Topic_Diversity': 0.775}


# ClusterTM

### 참조 : https://aclanthology.org/2020.emnlp-main.135/
### Github : https://github.com/adalmia96/Cluster-Analysis

In [35]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import KMeans
import numpy as np

# 전처리된 문서 리스트 (예: train_total_text_list)
documents = train_total_text_list

# TF-IDF 벡터 생성
tfidf_vectorizer = TfidfVectorizer(stop_words='english')
tfidf_matrix = tfidf_vectorizer.fit_transform(documents)

# KMeans 클러스터링 수행
n_clusters = 20
kmeans = KMeans(n_clusters=n_clusters, random_state=0)
kmeans.fit(tfidf_matrix)

# 각 클러스터의 대표 단어 추출
order_centroids = kmeans.cluster_centers_.argsort()[:, ::-1]
terms = tfidf_vectorizer.get_feature_names_out()

cluster_topics = []
for i in range(n_clusters):
    top_words = [terms[ind] for ind in order_centroids[i, :10]]
    cluster_topics.append(top_words)
    print(f"Cluster {i}: {top_words}")


Cluster 0: ['pandemic', 'coronavirus', 'sports', 'amid', 'workers', 'leagues', 'world', 'homebound', 'new', 'employee']
Cluster 1: ['president', 'trump', 'coronavirus', 'new', 'know', 'biden', 'thanks', 'like', 'does', 'don']
Cluster 2: ['indoor', 'olympic', 'athens', 'holmes', 'world', 'championships', 'athletics', 'kenteris', 'race', 'champion']
Cluster 3: ['covid', '19', 'beat', 'pts', 'period', 'overtime', 'islanders', 'pp', 'scorer', 'steelers']
Cluster 4: ['england', 'game', 'said', 'chelsea', 'players', 'rugby', 'win', 'france', 'club', 'wales']
Cluster 5: ['mobile', 'phone', 'phones', 'mobiles', 'said', '3g', 'music', 'people', 'technology', 'handsets']
Cluster 6: ['games', 'said', 'music', 'digital', 'sony', 'technology', 'nintendo', 'video', 'people', 'game']
Cluster 7: ['said', 'law', 'eu', 'government', 'mr', 'rights', 'police', 'lords', 'uk', 'human']
Cluster 8: ['lord', 'answer', 'said', 'advice', 'legal', 'war', 'general', 'goldsmith', 'attorney', 'action']
Cluster 9: ['

In [36]:
import numpy as np
import pandas as pd
from sklearn.metrics import mutual_info_score

# 테스트 데이터셋 준비 및 클러스터 라벨 추출
test_tfidf_matrix = tfidf_vectorizer.transform(test_total_text_list)
test_topic_labels = kmeans.predict(test_tfidf_matrix)

# 플랫폼 라벨 준비
test_platform_labels = [testds[i][-1] for i in range(len(testds))]

# 플랫폼별 토픽 분포 계산
topic_dist_df_test = pd.crosstab(pd.Series(test_topic_labels, name='Topic'),
                                 pd.Series(test_platform_labels, name='Platform'), normalize='index')

# 전체 데이터셋에 대한 토픽 분포의 엔트로피 계산 (H(Y))
topic_probabilities = pd.Series(test_topic_labels).value_counts(normalize=True)
H_Y = -np.sum(topic_probabilities * np.log(topic_probabilities + 1e-10))

# 각 플랫폼별 조건부 엔트로피 계산 및 H(Y|X) 계산
H_Y_given_X_total = 0
platform_probabilities = pd.Series(test_platform_labels).value_counts(normalize=True)
for platform in platform_probabilities.index:
    platform_indices = [i for i, x in enumerate(test_platform_labels) if x == platform]
    platform_topic_labels = [test_topic_labels[i] for i in platform_indices]
    platform_topic_prob = pd.Series(platform_topic_labels).value_counts(normalize=True)
    H_Y_given_X = -np.sum(platform_topic_prob * np.log(platform_topic_prob + 1e-10))
    H_Y_given_X_total += platform_probabilities[platform] * H_Y_given_X

# 상호정보량(MI) 계산
mi = H_Y - H_Y_given_X_total

# 플랫폼 분포의 엔트로피 H(X) 계산
H_X = -np.sum(platform_probabilities * np.log(platform_probabilities + 1e-10))

# 정규화된 상호정보량(NMI) 계산
NMI = 2 * mi / (H_Y + H_X)

print("Normalized Mutual Information (NMI):", NMI)
print('H(Y):', H_Y)
print('H(Y|X):', H_Y_given_X_total)
print('Mutual Information (MI):', mi)


Normalized Mutual Information (NMI): 0.29761668006677094
H(Y): 1.9727685671943447
H(Y|X): 1.5157287746570696
Mutual Information (MI): 0.4570397925372751


ValueError: Found input variables with inconsistent numbers of samples: [720, 715]

In [81]:
# 문서의 클러스터 할당
document_clusters = kmeans.labels_

# 클러스터별 라벨 데이터 수집
cluster_labels = [[] for _ in range(n_clusters)]
for doc_idx, cluster_idx in enumerate(document_clusters):
    label = train_total_label_list[doc_idx]  # 문서에 해당하는 라벨
    cluster_labels[cluster_idx].append(label)

# 라벨 순도 계산 함수는 이전에 제공된 calculate_label_purity 함수를 그대로 사용합니다.

# 라벨 순도 계산
purity_scores_cluster, average_purity_cluster = calculate_label_purity(cluster_labels)

print("각 클러스터의 라벨 순도:", purity_scores_cluster)
print("평균 라벨 순도:", average_purity_cluster)


각 클러스터의 라벨 순도: [0.4745762711864407, 0.3744333635539438, 1.0, 0.5675675675675675, 0.9818181818181818, 1.0, 0.9887640449438202, 0.8923076923076924, 0.5645161290322581, 0.8235294117647058, 1.0, 1.0, 0.953125, 1.0, 0.9830508474576272, 0.9612403100775194, 0.36, 0.46835443037974683, 1.0, 0.8438818565400844]
평균 라벨 순도: 0.8118582553314795


# Cluster TM coherence

In [37]:
topics = cluster_topics

## ALL

In [36]:
print(get_topic_coherence(topics, texts))

{'NPMI': 0.20008501517666222, 'UCI': 0.9055714802921859, 'UMASS': -2.36348362774683, 'CV': 0.8230549998040948, 'Topic_Diversity': 0.465}


## BBC

In [38]:
print(get_topic_coherence(topics, bbc_texts))

{'NPMI': 0.21137072598219792, 'UCI': 0.7716144245481134, 'UMASS': -1.6060574901800002, 'CV': 0.691863448246452, 'Topic_Diversity': 0.8}


## NYT

In [39]:
print(get_topic_coherence(topics, nyt_texts))

{'NPMI': 0.4902062075816128, 'UCI': 2.473537331123241, 'UMASS': -1.3115843132169915, 'CV': 0.642560247317548, 'Topic_Diversity': 0.8}


## 20NEWS

In [40]:
print(get_topic_coherence(topics, news_texts))

{'NPMI': 0.2976138687789487, 'UCI': 1.465343942906253, 'UMASS': -1.6929572550389256, 'CV': 0.6334462608662739, 'Topic_Diversity': 0.8}


# Top2vec

!pip install numpy==1.24

In [33]:
# from top2vec import Top2Vec

# # 트레인 데이터 로드
# # 여기서는 train_total_text_list가 트레인 데이터의 텍스트 리스트라고 가정합니다.
# documents = train_total_text_list

# # Top2Vec 모델 학습
# # speed='deep-learn'은 더 정확한 모델을 위해 더 많은 시간이 걸릴 수 있습니다.
# # workers는 사용할 CPU 코어 수입니다. -1은 모든 코어를 사용한다는 의미입니다.
# model = Top2Vec(documents, speed="deep-learn", workers=-1)

# # 학습된 모델에서 20개의 토픽에 대한 상위 10개 토픽 워드 추출
# topic_words, word_scores, topic_nums = model.get_topics(num_topics=20)

# # 각 토픽별 워드 리스트를 저장할 빈 리스트 생성
# top_10_word_lists = []

# for words in topic_words:
#     # 각 토픽에서 상위 10개 단어만 선택
#     top_10_words = words[:10]
#     top_10_word_lists.append(top_10_words)

# # 결과 출력
# for i, word_list in enumerate(top_10_word_lists):
#     print(f"토픽 {i+1}의 상위 10개 워드:")
#     print(word_list)
#     print("\n")

ImportError: Numba needs NumPy 1.24 or less

In [44]:
from top2vec import Top2Vec
import random

np.random.seed(41)
random.seed(41)

# 트레인 데이터 로드
# 여기서는 train_total_text_list가 트레인 데이터의 텍스트 리스트라고 가정합니다.
documents = train_total_text_list

# Top2Vec 모델 학습
# speed='deep-learn'은 더 정확한 모델을 위해 더 많은 시간이 걸릴 수 있습니다.
# workers는 사용할 CPU 코어 수입니다. -1은 모든 코어를 사용한다는 의미입니다.
model = Top2Vec(documents, speed="deep-learn", workers=-1)

# 학습된 모델에서 20개의 토픽에 대한 상위 10개 토픽 워드 추출
topic_words, word_scores, topic_nums = model.get_topics(num_topics=20)

# 각 토픽별 워드 리스트를 저장할 빈 리스트 생성
top_10_word_lists = []

for words in topic_words:
    # 각 토픽에서 상위 10개 단어만 선택
    top_10_words = words[:10]
    top_10_word_lists.append(top_10_words)

# 결과 출력
for i, word_list in enumerate(top_10_word_lists):
    print(f"토픽 {i+1}의 상위 10개 워드:")
    print(word_list)
    print("\n")

2024-03-14 22:51:08,737 - top2vec - INFO - Pre-processing documents for training
INFO:top2vec:Pre-processing documents for training
2024-03-14 22:51:10,334 - top2vec - INFO - Downloading universal-sentence-encoder-multilingual model
INFO:top2vec:Downloading universal-sentence-encoder-multilingual model
2024-03-14 22:51:14,076 - top2vec - INFO - Creating joint document/word embedding
INFO:top2vec:Creating joint document/word embedding
2024-03-14 22:51:19,012 - top2vec - INFO - Creating lower dimension embedding of documents
INFO:top2vec:Creating lower dimension embedding of documents
2024-03-14 22:51:34,595 - top2vec - INFO - Finding dense areas of documents
INFO:top2vec:Finding dense areas of documents
2024-03-14 22:51:34,664 - top2vec - INFO - Finding topics
INFO:top2vec:Finding topics


토픽 1의 상위 10개 워드:
['technologies' 'broadband' 'technology' 'gadgets' 'piracy' 'microsoft'
 'sony' 'tech' 'gadget' 'uk']


토픽 2의 상위 10개 워드:
['parliament' 'politicians' 'ministers' 'parliamentary' 'election'
 'minister' 'conservatives' 'britain' 'tories' 'voters']


토픽 3의 상위 10개 워드:
['genocide' 'israeli' 'guns' 'terrorism' 'armenians' 'israel' 'democrats'
 'weapons' 'conservatives' 'dems']


토픽 4의 상위 10개 워드:
['windows' 'mac' 'software' 'microsoft' 'files' 'ftp' 'programs' 'pcs'
 'window' 'monitor']


토픽 5의 상위 10개 워드:
['trump' 'democrats' 'dems' 'election' 'president' 'voters'
 'conservatives' 'politics' 'politicians' 'liberal']


토픽 6의 상위 10개 워드:
['baseball' 'pittsburgh' 'rangers' 'robinson' 'roddick' 'stadium' 'hockey'
 'championships' 'teams' 'team']


토픽 7의 상위 10개 워드:
['coronavirus' 'viruses' 'virus' 'dr' 'research' 'pandemic' 'soon'
 'recent' 'cases' 'recently']


토픽 8의 상위 10개 워드:
['hockey' 'pittsburgh' 'rangers' 'teams' 'premiership' 'team' 'robinson'
 'penalty' 'championships' 'leag

In [45]:
# 테스트 데이터에 대한 토픽 라벨과 점수를 얻기 위한 코드

# 빈 리스트를 초기화하여 각 테스트 데이터 항목의 토픽 라벨과 점수를 저장
test_topic_labels = []
test_data_topic_scores = []

# 테스트 데이터셋의 각 항목에 대해 반복
for text in test_total_text_list:
    # query_topics 메소드를 사용하여 각 텍스트에 대한 토픽 검색
    # 여기서는 가장 관련 있는 한 개의 토픽만 찾습니다(num_topics=1)
    topics_words, word_scores, topic_scores, topic_nums = model.query_topics(query=text, num_topics=1)
    
    # 찾아낸 토픽 번호와 점수를 리스트에 추가
    if topic_nums.size > 0:  # 토픽이 하나 이상 찾아진 경우
        test_topic_labels.append(topic_nums[0])
        test_data_topic_scores.append(topic_scores[0])
    else:  # 토픽을 찾지 못한 경우
        test_topic_labels.append(None)
        test_data_topic_scores.append(0)

# # 결과 출력
# for i, (label, score) in enumerate(zip(test_data_topic_labels, test_data_topic_scores)):
#     print(f"테스트 데이터 {i+1}: 토픽 라벨 = {label}, 점수 = {score}")

In [54]:
import numpy as np
import pandas as pd
from sklearn.metrics import mutual_info_score

# 가정: test_platform_labels는 준비되어 있음
# Top2Vec 모델을 사용하여 각 문서의 토픽 라벨을 추출합니다 (여기서는 이미 추출되어 있다고 가정)

# 플랫폼별 토픽 분포 계산
topic_dist_df_test = pd.crosstab(pd.Series(test_topic_labels, name='Topic'),
                                 pd.Series(test_platform_labels, name='Platform'), normalize='index')

# 플랫폼별 및 전체에 대한 토픽 분포를 계산
platform_counts = pd.Series(test_platform_labels).value_counts()
platform_probabilities = platform_counts / platform_counts.sum()

# 전체 데이터셋에 대한 토픽 분포의 엔트로피 계산 (H(Y))
topic_probabilities = pd.Series(test_topic_labels).value_counts(normalize=True)
H_Y = -np.sum(topic_probabilities * np.log(topic_probabilities + 1e-10))

# 각 플랫폼별 조건부 엔트로피 계산 및 H(Y|X) 계산
H_Y_given_X_total = 0
for platform in platform_probabilities.index:
    platform_indices = [i for i, x in enumerate(test_platform_labels) if x == platform]
    platform_topic_labels = [test_topic_labels[i] for i in platform_indices]
    platform_topic_prob = pd.Series(platform_topic_labels).value_counts(normalize=True)
    H_Y_given_X = -np.sum(platform_topic_prob * np.log(platform_topic_prob + 1e-10))
    H_Y_given_X_total += platform_probabilities[platform] * H_Y_given_X

# 상호정보량(MI) 및 정규화된 상호정보량(NMI) 계산
mi = H_Y - H_Y_given_X_total
H_X = -np.sum(platform_probabilities * np.log(platform_probabilities + 1e-10))
NMI = 2 * mi / (H_Y + H_X)

print("Normalized Mutual Information (NMI):", NMI)
print('H(Y):', H_Y)
print('H(Y|X):', H_Y_given_X_total)
print('Mutual Information (MI):', mi)


Normalized Mutual Information (NMI): 0.4587071942818904
H(Y): 2.749504402276371
H(Y|X): 1.866936239362655
Mutual Information (MI): 0.8825681629137159


ValueError: Found input variables with inconsistent numbers of samples: [720, 715]

In [83]:
from top2vec import Top2Vec
import logging

np.random.seed(41)
random.seed(41)

# 로깅 설정을 조정하여 Top2Vec의 내부 작업을 보다 자세히 볼 수 있습니다.
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

# 트레인 데이터 로드
documents = train_total_text_list  # train_total_text_list는 트레인 데이터의 텍스트 리스트입니다.

try:
    model = Top2Vec(documents, speed="deep-learn", workers=-1, 
                    umap_args={'n_neighbors': 25, 'n_components': 3, 'metric': 'cosine'}, 
                    hdbscan_args={'min_cluster_size': 10, 'metric': 'euclidean', 'cluster_selection_method': 'eom'})
except Exception as e:
    print(f"모델 학습 중 오류 발생: {e}")

# 학습된 모델에서 토픽 추출
# 추출된 토픽 수가 20개 미만일 경우, 추가 조정이 필요할 수 있습니다.
topic_words, word_scores, topic_nums = model.get_topics()

# 모델이 생성한 토픽 수를 확인하고, 20개 미만일 경우 로그나 경고 메시지 출력
print(f"모델이 생성한 토픽의 수: {len(topic_nums)}")
if len(topic_nums) < 20:
    print("경고: 요청한 20개의 토픽을 생성하지 못했습니다. 파라미터 조정이 필요할 수 있습니다.")

# 각 토픽별 워드 리스트를 저장할 빈 리스트 생성
top_10_word_lists = []

for words in topic_words:
    # 각 토픽에서 상위 10개 단어만 선택
    top_10_words = words[:10]
    top_10_word_lists.append(top_10_words)

# 결과 출력
for i, word_list in enumerate(top_10_word_lists):
    print(f"토픽 {i+1}의 상위 10개 워드:")
    print(word_list)
    print("\n")


2024-03-15 11:35:27,132 - top2vec - INFO - Pre-processing documents for training
INFO:top2vec:Pre-processing documents for training
2024-03-15 11:35:29,378 - top2vec - INFO - Downloading universal-sentence-encoder-multilingual model
INFO:top2vec:Downloading universal-sentence-encoder-multilingual model
2024-03-15 11:35:31,634 - top2vec - INFO - Creating joint document/word embedding
INFO:top2vec:Creating joint document/word embedding
2024-03-15 11:35:36,469 - top2vec - INFO - Creating lower dimension embedding of documents
INFO:top2vec:Creating lower dimension embedding of documents
2024-03-15 11:35:54,495 - top2vec - INFO - Finding dense areas of documents
INFO:top2vec:Finding dense areas of documents
2024-03-15 11:35:54,559 - top2vec - INFO - Finding topics
INFO:top2vec:Finding topics


모델이 생성한 토픽의 수: 27
토픽 1의 상위 10개 워드:
['technologies' 'broadband' 'technology' 'gadgets' 'piracy' 'microsoft'
 'sony' 'tech' 'gadget' 'spyware']


토픽 2의 상위 10개 워드:
['parliament' 'ministers' 'politicians' 'parliamentary' 'election'
 'minister' 'conservatives' 'britain' 'tories' 'voters']


토픽 3의 상위 10개 워드:
['windows' 'mac' 'software' 'microsoft' 'ftp' 'files' 'programs' 'pcs'
 'window' 'dvd']


토픽 4의 상위 10개 워드:
['trump' 'democrats' 'dems' 'election' 'president' 'voters'
 'conservatives' 'politics' 'politicians' 'liberal']


토픽 5의 상위 10개 워드:
['guns' 'weapons' 'gun' 'democrats' 'police' 'criminal' 'terrorism'
 'conservatives' 'crime' 'dems']


토픽 6의 상위 10개 워드:
['baseball' 'robinson' 'roddick' 'pittsburgh' 'rangers' 'hockey' 'stadium'
 'championships' 'teams' 'davis']


토픽 7의 상위 10개 워드:
['hockey' 'pittsburgh' 'rangers' 'teams' 'premiership' 'baseball' 'league'
 'championships' 'penalty' 'team']


토픽 8의 상위 10개 워드:
['coronavirus' 'viruses' 'virus' 'dr' 'pandemic' 'cases' 'soon' 'health'
 'exper

In [84]:
from collections import Counter

# 문서의 토픽 할당을 얻는 함수를 수정합니다.
def get_document_topic_assignments(model):
    # 모델에 저장된 모든 문서의 ID를 가져옵니다.
    document_ids = list(range(len(model.doc_top)))
    # 각 문서 ID에 대해 가장 관련이 높은 토픽을 조회합니다.
    doc_topics, doc_scores, topic_words, word_scores = model.get_documents_topics(doc_ids=document_ids, reduced=False)
    
    # 각 문서에 할당된 토픽 번호를 반환합니다.
    # doc_topics 자체가 각 문서에 할당된 토픽 번호의 배열이므로, 이를 직접 반환합니다.
    return doc_topics


# 문서에 할당된 토픽을 얻습니다.
document_topics = get_document_topic_assignments(model)

# 라벨 퓨리티를 계산하는 함수
def calculate_label_purity(documents, labels, document_topics):
    topic_label_mapping = [[] for _ in range(max(document_topics) + 1)]
    for doc_topic, label in zip(document_topics, labels):
        topic_label_mapping[doc_topic].append(label)
    
    purity_scores = []
    for topic_labels in topic_label_mapping:
        if topic_labels:
            most_common_label, count = Counter(topic_labels).most_common(1)[0]
            purity = count / len(topic_labels)
            purity_scores.append(purity)
    
    average_purity = sum(purity_scores) / len(purity_scores) if purity_scores else 0
    return purity_scores, average_purity

# 상위 20개 토픽에 대한 문서만 필터링 (상위 20개 토픽의 인덱스가 필요)
selected_topics = set(topic_nums[:20])
filtered_document_topics = [topic for topic in document_topics if topic in selected_topics]

# 라벨 퓨리티 계산
purity_scores, average_purity = calculate_label_purity(train_total_text_list, train_total_label_list, filtered_document_topics)

print("각 토픽의 라벨 퓨리티:", purity_scores)
print("평균 라벨 퓨리티:", average_purity)


각 토픽의 라벨 퓨리티: [0.9680511182108626, 0.9897959183673469, 0.6666666666666666, 0.8761904761904762, 0.951048951048951, 0.7627118644067796, 0.7610619469026548, 0.7522935779816514, 0.7789473684210526, 0.9666666666666667, 0.9887640449438202, 0.8648648648648649, 0.9841269841269841, 1.0, 0.9122807017543859, 0.9821428571428571, 0.9090909090909091, 0.8727272727272727, 0.8867924528301887, 0.8235294117647058]
평균 라벨 퓨리티: 0.8848877027054549


# Top2vec coherence

In [50]:
topics = top_10_word_lists

## ALL

In [43]:
print(get_topic_coherence(topics, texts))

{'NPMI': 0.1668010386041268, 'UCI': 1.303180851404751, 'UMASS': -3.5717694359332315, 'CV': 0.6191340052720784, 'Topic_Diversity': 0.53}


## BBC

In [51]:
print(get_topic_coherence(topics, bbc_texts))

{'NPMI': 0.2727238947657637, 'UCI': 1.1588736309605066, 'UMASS': -1.581955757886845, 'CV': 0.6443891991085016, 'Topic_Diversity': 0.65}


## NYT

In [52]:
print(get_topic_coherence(topics, nyt_texts))

{'NPMI': 0.5396986120725706, 'UCI': 2.8724360949087857, 'UMASS': -1.1979579661002924, 'CV': 0.717377253751532, 'Topic_Diversity': 0.65}


## 20NEWS

In [53]:
print(get_topic_coherence(topics, news_texts))

{'NPMI': 0.5004102665732146, 'UCI': 2.487407723292529, 'UMASS': -1.1545452600462238, 'CV': 0.7321346589118936, 'Topic_Diversity': 0.65}


# LDA 

In [60]:

reference_dictionary = Dictionary(reference_corpus)
dictionary=reference_dictionary

In [61]:
from gensim.models import LdaMulticore

train_texts = [doc.split() for doc in trainds.preprocess_ctm(trainds.nonempty_text)]

# corpus 생성 (훈련 데이터를 이용)
train_corpus = [dictionary.doc2bow(text) for text in train_texts]

# LDA 모델 훈련
lda_model = LdaMulticore(
    corpus=train_corpus,
    num_topics=20,
    id2word=dictionary,
    passes=10,
    workers=3,  
    random_state=41
)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [62]:
# 테스트 데이터로부터 토픽 워드 리스트 생성
train_topics_lda = lda_model.get_document_topics(train_corpus, minimum_probability=0)

train_topic_words_list_lda = [
    [dictionary[word_id] for word_id, prob in lda_model.get_topic_terms(topicid, topn=10)]
    for topicid in range(lda_model.num_topics)
]
# 기존 사전에 LDA 모델에서 생성된 테스트 토픽의 단어 추가
for topic_words in train_topic_words_list_lda:
    dictionary.add_documents([topic_words])

topics = train_topic_words_list_lda

In [65]:
texts=reference_corpus
test_texts = [doc.split() for doc in testds.preprocess_ctm(testds.nonempty_text)]  # 예시 데이터셋
test_corpus = [dictionary.doc2bow(text) for text in texts]

In [66]:
import numpy as np
import pandas as pd
from sklearn.metrics import mutual_info_score

# 테스트 데이터셋의 토픽 분포 예측
test_topic_distributions = [lda_model.get_document_topics(bow) for bow in test_corpus]

# 테스트 데이터셋의 각 문서에 대해 가장 높은 토픽 할당
test_topic_labels_lda = [max(dist, key=lambda x: x[1])[0] for dist in test_topic_distributions]

# 플랫폼 라벨 준비
test_platform_labels = [testds[i][-1] for i in range(len(testds))]

# 플랫폼별 토픽 분포 계산
topic_dist_df_test = pd.crosstab(pd.Series(test_topic_labels_lda, name='Topic'),
                                 pd.Series(test_platform_labels, name='Platform'), normalize='index')

# 전체 데이터셋에 대한 토픽 분포의 엔트로피 계산 (H(Y))
topic_probabilities = pd.Series(test_topic_labels_lda).value_counts(normalize=True)
H_Y = -np.sum(topic_probabilities * np.log(topic_probabilities + 1e-10))

# 각 플랫폼별 조건부 엔트로피 계산 및 H(Y|X) 계산
H_Y_given_X_total = 0
platform_probabilities = pd.Series(test_platform_labels).value_counts(normalize=True)
for platform in platform_probabilities.index:
    platform_indices = [i for i, x in enumerate(test_platform_labels) if x == platform]
    platform_topic_labels = [test_topic_labels_lda[i] for i in platform_indices]
    platform_topic_prob = pd.Series(platform_topic_labels).value_counts(normalize=True)
    H_Y_given_X = -np.sum(platform_topic_prob * np.log(platform_topic_prob + 1e-10))
    H_Y_given_X_total += platform_probabilities[platform] * H_Y_given_X

# 상호정보량(MI) 계산
mi = H_Y - H_Y_given_X_total

# 플랫폼 분포의 엔트로피 H(X) 계산
H_X = -np.sum(platform_probabilities * np.log(platform_probabilities + 1e-10))

# 정규화된 상호정보량(NMI) 계산
NMI = 2 * mi / (H_Y + H_X)

print("Normalized Mutual Information (NMI):", NMI)
print('H(Y):', H_Y)
print('H(Y|X):', H_Y_given_X_total)
print('Mutual Information (MI):', mi)

# Original Mutual Information Score 계산
mi_score = mutual_info_score(test_topic_labels_lda, test_platform_labels)
print("Original Mutual Information Score:", mi_score)


Normalized Mutual Information (NMI): 0.2324220762364051
H(Y): 2.6533559884617994
H(Y|X): 2.2173415563810295
Mutual Information (MI): 0.43601443208076995
Original Mutual Information Score: 0.43601443221433656


In [86]:
# 각 문서의 토픽 할당을 위한 함수
def assign_topics_to_documents(lda_model, corpus):
    topic_assignments = []
    for doc_bow in corpus:
        # 각 문서에 대한 토픽 분포를 얻음
        topic_distribution = lda_model.get_document_topics(doc_bow)
        # 가장 확률이 높은 토픽을 선택
        assigned_topic = max(topic_distribution, key=lambda x: x[1])[0]
        topic_assignments.append(assigned_topic)
    return topic_assignments

def calculate_label_purity(topic_labels):
    purity_scores = []
    
    for labels in topic_labels:
        if not labels:
            continue
        most_common_label = max(set(labels), key=labels.count) 
        purity = labels.count(most_common_label) / len(labels)
        purity_scores.append(purity)

    average_purity = sum(purity_scores) / len(purity_scores) if purity_scores else 0
    return purity_scores, average_purity

# 문서에 대한 토픽 할당
document_topics = assign_topics_to_documents(lda_model, train_corpus)

# 토픽별 라벨 데이터 수집 (라벨 데이터는 train_labels_list에 있다고 가정)
topic_labels_lda = [[] for _ in range(lda_model.num_topics)]
for doc_idx, topic in enumerate(document_topics):
    label = train_total_label_list[doc_idx]  # 문서에 해당하는 라벨
    topic_labels_lda[topic].append(label)

# label purity 계산
purity_scores_lda, average_purity_lda = calculate_label_purity(topic_labels_lda)

print("LDA 각 토픽의 라벨 순도:", purity_scores_lda)
print("LDA 평균 라벨 순도:", average_purity_lda)


LDA 각 토픽의 라벨 순도: [0.5714285714285714, 0.8413284132841329, 0.8640776699029126, 0.8680555555555556, 0.5625, 0.4594594594594595, 0.5545454545454546, 0.4792626728110599, 0.5337423312883436, 0.6864864864864865, 0.5342465753424658, 0.4166666666666667, 0.8, 0.46153846153846156, 0.5903614457831325, 0.8347457627118644, 0.5111111111111111, 0.54, 0.75, 0.56]
LDA 평균 라벨 순도: 0.620977831895784


In [67]:
print(get_topic_coherence(topics, bbc_texts))

{'NPMI': 0.1944986739563538, 'UCI': 0.6747626954303296, 'UMASS': -1.4725600476309897, 'CV': 0.605449541143632, 'Topic_Diversity': 0.71}


In [68]:
print(get_topic_coherence(topics, nyt_texts))

{'NPMI': 0.47769920895523954, 'UCI': 2.4681887696724494, 'UMASS': -1.370101734065157, 'CV': 0.6192546265712999, 'Topic_Diversity': 0.71}


In [69]:
print(get_topic_coherence(topics, news_texts))

{'NPMI': 0.27018213638657607, 'UCI': 1.1949787495647093, 'UMASS': -1.7652447167655498, 'CV': 0.6420283890748638, 'Topic_Diversity': 0.71}


In [96]:
from bertopic import BERTopic

bert_train_texts = [' '.join(doc) if isinstance(doc, list) else doc for doc in train_texts]

# BERTopic 모델 훈련
bertopic_model = BERTopic(language="english", calculate_probabilities=True, nr_topics=21, verbose=True)
bertopic_model.fit(bert_train_texts)

# 각 토픽별 상위 10개 단어 추출
topics = bertopic_model.get_topics()

# 상위 10개 단어를 포함하는 토픽 리스트 생성
topk_topic_words_list = []
for topic_num, topic in topics.items():
    if topic_num != -1:  # -1은 outlier 토픽을 의미합니다.
        topk_words = [word for word, _ in topic[:10]]
        topk_topic_words_list.append(topk_words)

2024-03-15 13:58:59,422 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/81 [00:00<?, ?it/s]

2024-03-15 13:59:04,207 - BERTopic - Embedding - Completed ✓
2024-03-15 13:59:04,208 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-03-15 13:59:17,286 - BERTopic - Dimensionality - Completed ✓
2024-03-15 13:59:17,288 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-03-15 13:59:17,532 - BERTopic - Cluster - Completed ✓
2024-03-15 13:59:17,533 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-03-15 13:59:17,973 - BERTopic - Representation - Completed ✓
2024-03-15 13:59:17,974 - BERTopic - Topic reduction - Reducing number of topics
2024-03-15 13:59:18,393 - BERTopic - Topic reduction - Reduced number of topics from 37 to 21


In [111]:
label_to_num = {'politics': 0, 'sport': 1, 'tech': 2}

# BERTopic 모델 훈련
bertopic_model = BERTopic(language="english", calculate_probabilities=True, verbose=True, nr_topics=21)
bertopic_model.fit(bert_train_texts)

# 테스트 데이터셋의 토픽 할당
topics, probs = bertopic_model.transform(bert_test_texts)

# 토픽별 문서 수 계산 (노이즈 토픽 -1 제외)
topic_counts = Counter(topics)

# 노이즈 토픽(-1) 포함 상위 21개 토픽 선택
top_21_topics = [topic for topic, count in topic_counts.most_common(21)]

# 노이즈 토픽 제거
if -1 in top_21_topics:
    top_21_topics.remove(-1)
test_target_bert = [label_to_num[label] for label in test_total_label_list]

# 상위 토픽에 해당하는 문서의 확률과 라벨만 필터링 (노이즈 토픽 제외)
filtered_probs = np.array([probs[i] for i, topic in enumerate(topics) if topic in top_21_topics])
filtered_labels = [test_target_bert[i] for i, topic in enumerate(topics) if topic in top_21_topics]

def calculate_label_purity(filtered_labels, top_20_topics, topics):
    """
    각 토픽의 label purity를 계산합니다.
    
    :param filtered_labels: 상위 20개 토픽에 해당하는 문서의 라벨
    :param top_20_topics: 상위 20개 토픽의 ID 리스트
    :param topics: 모든 문서에 할당된 토픽 ID 리스트
    :return: 각 토픽의 label purity 리스트와 평균 label purity
    """
    topic_label_mapping = {topic: [] for topic in top_20_topics}
    
    # 각 토픽에 대한 라벨 할당
    for label, topic in zip(filtered_labels, topics):
        if topic in top_20_topics:
            topic_label_mapping[topic].append(label)
    
    purity_scores = []
    for topic, labels in topic_label_mapping.items():
        if labels:
            most_common_label, count = Counter(labels).most_common(1)[0]
            purity = count / len(labels)
            purity_scores.append(purity)
    
    average_purity = np.mean(purity_scores) if purity_scores else 0
    return purity_scores, average_purity

# BERTopic에 대한 label purity 계산
purity_scores_bertopic, average_purity_bertopic = calculate_label_purity(filtered_labels, top_21_topics, topics)

print("BERTopic 각 토픽의 label purity:", purity_scores_bertopic)
print("BERTopic 평균 label purity:", average_purity_bertopic)

2024-03-15 15:15:40,997 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/81 [00:00<?, ?it/s]

2024-03-15 15:15:44,532 - BERTopic - Embedding - Completed ✓
2024-03-15 15:15:44,533 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-03-15 15:16:00,930 - BERTopic - Dimensionality - Completed ✓
2024-03-15 15:16:00,932 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-03-15 15:16:01,233 - BERTopic - Cluster - Completed ✓
2024-03-15 15:16:01,235 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-03-15 15:16:01,880 - BERTopic - Representation - Completed ✓
2024-03-15 15:16:01,882 - BERTopic - Topic reduction - Reducing number of topics
2024-03-15 15:16:02,428 - BERTopic - Topic reduction - Reduced number of topics from 40 to 21


Batches:   0%|          | 0/23 [00:00<?, ?it/s]

2024-03-15 15:16:03,431 - BERTopic - Dimensionality - Reducing dimensionality of input embeddings.
2024-03-15 15:16:10,871 - BERTopic - Dimensionality - Completed ✓
2024-03-15 15:16:10,873 - BERTopic - Clustering - Approximating new points with `hdbscan_model`
2024-03-15 15:16:10,902 - BERTopic - Probabilities - Start calculation of probabilities with HDBSCAN
2024-03-15 15:16:11,022 - BERTopic - Probabilities - Completed ✓
2024-03-15 15:16:11,023 - BERTopic - Cluster - Completed ✓


BERTopic 각 토픽의 label purity: [0.9117647058823529, 0.975609756097561, 1.0, 0.8235294117647058, 0.7, 0.6666666666666666, 0.5714285714285714, 1.0, 1.0, 1.0, 0.5, 1.0]
BERTopic 평균 label purity: 0.8457499259866549


In [98]:
print(get_topic_coherence(topk_topic_words_list, bbc_texts))

{'NPMI': 0.23755793281902068, 'UCI': 1.0468743342605904, 'UMASS': -1.5080627212039504, 'CV': 0.6828528664401331, 'Topic_Diversity': 0.885}


In [99]:
print(get_topic_coherence(topk_topic_words_list, nyt_texts))

{'NPMI': 0.5003199543912695, 'UCI': 2.580250171038324, 'UMASS': -1.3296507581506674, 'CV': 0.6783082573932905, 'Topic_Diversity': 0.885}


In [100]:
print(get_topic_coherence(topk_topic_words_list, news_texts))

{'NPMI': 0.45145352171890557, 'UCI': 2.315469548089201, 'UMASS': -1.2263578881772255, 'CV': 0.6138534239173554, 'Topic_Diversity': 0.885}
